In [2]:
from gensim import downloader

vec_num = 50
GLOVE_PATH = f'glove-twitter-{vec_num}'
glove_twitter = downloader.load(GLOVE_PATH)
# glove_wiki = downloader.load('glove-wiki-gigaword-300')


In [ ]:
import torch
def get_glove_vectors_in_batches_cuda(word_list, batch_size):
    device = torch.device("cuda" if torch.cuda.is_available() else "cpu")
    num_batches = (len(word_list) + batch_size - 1) // batch_size
    glove_vectors = []
    for i in range(num_batches):
        start_idx = i * batch_size
        end_idx = min((i + 1) * batch_size, len(word_list))
        batch_words = word_list[start_idx:end_idx]
        batch_vectors = [torch.tensor(glove_model.get_vector(word), device=device) for word in batch_words]
        glove_vectors.extend(batch_vectors)
    return glove_vectors

In [20]:
import numpy as np

def open_and_split_file(file_path, is_train=True):
    with open(file_path) as f:
        lines = f.readlines()
        words = []
        tags = []
        for line in lines:
            # get_glove_vectors_in_batches_cuda(lines, 1000)
            try:
                word, tag = line.rstrip().split("\t")
                word = word.lower()
                # words.append(word)
                print(word)
                if is_train:
                    if (word not in glove_twitter):
                        words.append(np.zeros(vec_num))
                        # continue
                        # glove_twitter[word] = np.zeros(vec_num)
                    else:
                        words.append(glove_twitter[word])
                else:
                    if (word not in glove_twitter):
                        words.append(np.zeros(vec_num))
                    else:
                        words.append(glove_twitter[word])
                tags.append(0 if tag == "O" else 1)

            except:
                continue
    return words, tags

In [21]:
train_words, train_labels = open_and_split_file("/home/student/hw2/NER_task_in_NLP/data/train.tagged")

@paulwalk
it
's
the
view
from
where
i
'm
living
for
two
weeks
.
empire
state
building
=
esb
.
pretty
bad
storm
here
last
evening
.
from
green
newsfeed
:
ahfa
extends
deadline
for
sage
award
to
nov
.
5
http://tinyurl.com/24agj38
pxleyes
top
50
photography
contest
pictures
of
august
2010
...
http://bit.ly/bgcyz0
#photography
today
is
my
last
day
at
the
office
.
4dbling
's
place
til
monday
,
party
party
party
.
&lt;
3
watching
the
vma
pre-show
again
lol
it
was
n't
even
a
good
show
the
first
time
...
so
bored
!
27
followers
!
30
followers
is
my
goal
for
today
!
this
is
the
2nd
hospital
ive
been
in
today
,
but
ive
just
seen
a
doctor
who
was
an
older
version
of
justin
:'
)
friday
night
eats
http://twitpic.com/2pdvtr
gotta
dress
up
for
london
fashion
week
and
party
in
style
!
@suzie55
whispering
cause
i
may
have
had
1
too
many
vodka
's
last
night
and
am
a
lil
fragile
,
hold
me
?
#nfl
week
2
picks
blog
is
up
on
@the_score
website
...
http://blogs.thescore.com/nfl/2010/09/17/pizzolaw2/
i
like
@

In [22]:
dev_words, dev_labels = open_and_split_file("/home/student/hw2/NER_task_in_NLP/data/dev.tagged", is_train=False)

stabilized
approach
or
not
?
that
´
s
insane
and
good
.
you
should
'
ve
stayed
on
redondo
beach
blvd
.
you
were
in
the
borderlines
of
gardena
/
compton
all
i
'
ve
been
doing
is
binge
watching
rick
and
morty
😂
wow
emma
and
kaite
is
so
very
cute
and
so
funny
😀
😀
😀
😗
😘
i
wish
im
ryan
😭
😭
😭
this
is
so
good
trump
is
the
kremlin
'
s
boy
hobby
frog
is
a
savege
creepy
af
.
lol
these
trap
came
from
taiwan
.
idiot
needs
to
be
punched
in
the
throat
,
he
has
no
business
with
a
kitten
or
a
baby
,
a
donkey
punch
to
the
back
of
his
head
is
warranted
as
well
,
fucking
moron
!
mine
is
a
skin
product
but
i
never
need
any
moisturizer
or
primer
in
the
morning
.
it
'
s
called
ha
5
.
it
'
s
amazing
.
takes
my
dark
circles
and
puffiness
away
!
makeup
lays
beautiful
over
it
!
had
to
mute
this
because
she
sounds
so
dumb
warriors
looked
a
little
bored
,
gave
a
c
plus
effort
and
got
the
win
.
.
.
this
should
be
short
and
sweet
.
wow
smh
envy
nails
are
so
clean
and
long
,
thought
they
were
fake
everyday
i
'
m
mor

In [23]:
from sklearn.neighbors import KNeighborsClassifier

knn = KNeighborsClassifier(n_neighbors=9)
knn.fit(train_words, train_labels)
y_pred = knn.predict(dev_words)

from sklearn.metrics import f1_score
f1_score(dev_labels, y_pred, average='macro')

/anaconda/envs/azureml_py38/lib/python3.8/site-packages/sklearn/neighbors/_classification.py:228: FutureWarning: Unlike other reduction functions (e.g. `skew`, `kurtosis`), the default behavior of `mode` typically preserves the axis it acts along. In SciPy 1.11.0, this behavior will change: the default value of `keepdims` will become False, the `axis` over which the statistic is taken will be eliminated, and the value None will no longer be accepted. Set `keepdims` to True or False to avoid this warning.
  mode, _ = stats.mode(_y[neigh_ind, k], axis=1)


0.7795417689682522

In [25]:
len([y for y in y_pred if y != 0])

678

## Some kaki

In [11]:
from tqdm import tqdm
import torch
 
train_path = "/home/student/hw2/NER_task_in_NLP/data/train.tagged"
word_tag_dict = dict()
# open_and_split_file(train_path, word_tag_dict)

train_dataset = torch.zeros((len(words), vec_dim), dtype=torch.float32)
if torch.cuda.is_available():
    train_dataset = train_dataset.cuda()

for i, word in tqdm(enumerate(words)):
    if word not in glove_twitter:
        glove_twitter[word] = np.zeros(vec_dim)
    print(word)
    train_dataset[i] = torch.from_numpy(glove_twitter[word])



62730it [00:00, 2116859.41it/s]


[0,
 1,
 2,
 3,
 4,
 5,
 6,
 7,
 8,
 9,
 10,
 11,
 12,
 13,
 14,
 15,
 16,
 17,
 18,
 19,
 20,
 21,
 22,
 23,
 24,
 25,
 26,
 27,
 28,
 29,
 30,
 31,
 32,
 33,
 34,
 35,
 36,
 37,
 38,
 39,
 40,
 41,
 42,
 43,
 44,
 45,
 46,
 47,
 48,
 49,
 50,
 51,
 52,
 53,
 54,
 55,
 56,
 57,
 58,
 59,
 60,
 61,
 62,
 63,
 64,
 65,
 66,
 67,
 68,
 69,
 70,
 71,
 72,
 73,
 74,
 75,
 76,
 77,
 78,
 79,
 80,
 81,
 82,
 83,
 84,
 85,
 86,
 87,
 88,
 89,
 90,
 91,
 92,
 93,
 94,
 95,
 96,
 97,
 98,
 99,
 100,
 101,
 102,
 103,
 104,
 105,
 106,
 107,
 108,
 109,
 110,
 111,
 112,
 113,
 114,
 115,
 116,
 117,
 118,
 119,
 120,
 121,
 122,
 123,
 124,
 125,
 126,
 127,
 128,
 129,
 130,
 131,
 132,
 133,
 134,
 135,
 136,
 137,
 138,
 139,
 140,
 141,
 142,
 143,
 144,
 145,
 146,
 147,
 148,
 149,
 150,
 151,
 152,
 153,
 154,
 155,
 156,
 157,
 158,
 159,
 160,
 161,
 162,
 163,
 164,
 165,
 166,
 167,
 168,
 169,
 170,
 171,
 172,
 173,
 174,
 175,
 176,
 177,
 178,
 179,
 180,
 181,
 182,
 183,
 184,


In [3]:
def create_glove_vector_old(word, data):
    temp_word = False
    if word not in glove_twitter.key_to_index:
        # print(f"{word} not an existing word in the model")
        # if you dont have this word - just skip it
        # return False
        
        if word.startswith("http"):
            # all links in train data are tagged O
            data.append(np.zeros(vec_dim))
            return
        
        try:
            # check if word is a number
            float(word)
            data.append(np.zeros(vec_dim))
            return
        except:
            pass
    
        # try stemming
        for i in range(min(len(word), 5)):
            if word[i:] in glove_twitter.key_to_index:
                temp_word = word[i:]
                break
            for j in range(1, min(len(word), 5)):
                if word[i:-j] in glove_twitter.key_to_index:
                    temp_word = word[i:-j]
                    break

    else:
        temp_word = word


    if temp_word:
        vec = glove_twitter[temp_word]
        data.append(vec)

    else:
        data.append(np.zeros(vec_dim))
        # print(word)
    

In [5]:
from KNN import KnnClassifier

knn = KnnClassifier(9, 2)
train = np.array(train_dataset)
labels = np.array(train_labels)
print(len(train))
knn.fit(train, labels)
pred = knn.predict(train)

sum(np.array(train_labels).equal(pred)) / len(pred)

In [6]:
with open("/home/student/hw2/NER_task_in_NLP/data/train.tagged") as f:
    lines = f.readlines()
    words_count = 0
    prev_word = ''
    for i, line in enumerate(lines):
        try:
            word, tag = line.rstrip().split("\t")
            words_count += 1
            if  (word.startswith('http')):
                # print(tag)
                if tag != 'O': #and lines[i+1].rstrip().split('\t')[0] == ':':
                    print("yes")
                    print(word)
            #if line[i-1] != "\t\n" and "@" in word:#  \
            #and line[i-1].rstrip().split("\t")[0] == "RT" and line[i+1].rstrip().split("\t")[0] == ":":
                # print(line[i-1])
                #pass

        except:
            # print(line.rstrip().split("\t"))
            # # print(line)
            # print([line])
            # ! the line is blank representing \t\n
            # TODO thingy for end of sentence
            prev_word = ''
            continue
        prev_word = word

In [7]:
train_dataset

[array([-0.76609  ,  0.064331 ,  0.089665 ,  0.56744  ,  0.56519  ,
         0.28075  , -1.0013   , -0.34225  , -0.54118  ,  1.016    ,
        -0.7575   , -0.46685  ,  0.18454  , -0.3255   , -0.50096  ,
         0.28631  , -0.15541  , -0.14687  , -0.71308  , -0.26913  ,
        -0.0709   ,  0.019742 ,  0.03214  ,  0.52745  , -0.12772  ,
         0.097247 , -0.61656  , -0.84045  , -0.03508  , -0.0097963,
        -0.10188  ,  0.29714  ,  0.62053  , -0.087639 , -0.48333  ,
         0.041414 ,  0.10176  , -0.52762  , -0.46026  , -0.44252  ,
        -0.50563  , -0.57252  ,  1.03     ,  0.4256   , -0.78631  ,
         0.13241  , -0.20176  , -0.010587 ,  0.36891  , -0.066368 ,
        -0.038336 ,  0.55437  , -0.07356  ,  0.64697  ,  0.54841  ,
        -0.69994  ,  0.38874  , -0.62535  ,  0.53079  ,  0.33201  ,
        -0.38389  ,  0.1225   ,  0.012708 , -0.38007  , -0.12268  ,
         0.044718 , -0.15191  ,  0.12114  , -0.7289   , -0.26746  ,
        -0.28038  ,  0.21726  , -0.067307 , -0.1

In [17]:
from FeedForward import FeedForwardNN as ff
import torch
from torch.optim import Adam

In [24]:
train = torch.tensor(train_dataset).type(torch.FloatTensor)
labels = torch.tensor(train_labels).type(torch.FloatTensor)
datasets = {"train": train, "test": train}
model = ff.Neural_Network(vec_dim, 2)
optimizer = Adam(params=model.parameters())
train(model=model, data_sets=datasets, optimizer=optimizer, num_epochs=15)


RuntimeError: mat1 and mat2 shapes cannot be multiplied (62730x62730 and 1x6)